In [ ]:
import requests, pymongo, json, time
from datetime import datetime
from dateutil.relativedelta import relativedelta
from bs4 import BeautifulSoup

In [ ]:
api_key_path = "C:/Users/proth/Desktop/Thesis/data/NYT_API.key.txt"
with open(api_key_path, 'r') as handle:
    API_KEY = handle.read()
NYT_URL = 'http://api.nytimes.com/svc/search/v2/articlesearch.json'

In [ ]:
def call_api(url, payload, p=0):
    # Add the 'page' parameter to the payload.
    payload['page'] = p

    # Get the requested url. Error handling for bad requests should be done in
    # the calling function.
    return requests.get(url, params=payload)

In [ ]:
def get_response(r):
    # Use json.loads to read the response text
    raw = json.loads(r.text)

    # Return the meta (hits, etc.) and docs (containing urls'n'stuff) back
    return raw['response']['meta'], raw['response']['docs']

In [ ]:
def get_soup(url):
    # Header to be passed in to NYT when scraping article text.
    agent = 'DataWrangling/1.1; '
    agent += 'monsuralirana@gmail.com)'
    headers = {'user_agent': agent}

    # Wrap in a try-except to prevent a maxTry connection error from erroring
    # out the program. Return None if there are any issues.
    try:
        r = requests.get(url, headers=headers)
    except:
        return None

    # Just in case there was a normal error returned. Pass back None.
    if r.status_code != 200: return None

    # Otherwise return a soupified object containing the url text encoded in
    # utf-8. Will toss back errors on some pages without the encoding in place.
    return BeautifulSoup(r.text.encode('utf-8'), features="lxml")

In [ ]:
def get_body_text(docs):
    # Grab the url from each document, if it exists, then scrape each url for
    # its body text. If we get any errors along the way, continue on to the
    # next document / url to be scraped.
    result = []
    for d in docs:
        # article_dict = {}
        # Make a copy of the doc's dictionary
        doc = d.copy()
        # If there's no url (not sure why this happens sometimes) then ditch it
        if not doc['web_url']:
            continue

        # Scrape the doc's url, return a soup object with the url's text.
        soup = get_soup(doc['web_url'])
        if not soup:
            continue



        # Find all of the paragraphs with the correct class.
        # This class tag is specific to NYT articles.
        body = soup.find_all('div', class_="StoryBodyCompanionColumn")
        if not body:
            continue

        # Join the resulting body paragraphs' text (returned in a list).
        doc['body'] = '\n'.join([x.get_text() for x in body])

        print(doc['web_url'])
        result.append(doc)

    return result


In [ ]:
def remove_previously_scraped(coll, docs):
    # Check to see if the mongo collection already contains the docs returned
    # from NYT. Return back a list of the ones that aren't in the collection to
    # be scraped.
    new_docs = []
    for doc in docs:
        # Check fo the document id in mongo. If it finds none, append to
        # new_docs
        #cursor = articles.find({'_id': doc['_id']}).limit(1)
        if not articles.count_documents(filter={'_id': doc['_id']}) > 0:
            new_docs.append(doc)

    if new_docs == []:
        return None

    return new_docs


def get_end_date(dt):
    # String-ify the datetime object to YYYMMDD, which the NYT likes.
    yr = str(dt.year)
    mon = '0' * (2 - len(str(dt.month))) + str(dt.month)
    day = '0' * (2 - len(str(dt.day))) + str(dt.day)
    return yr + mon + day

In [ ]:
def scrape_articles(coll, last_date):
    page = 0
    while page <= 300:
        print('Page:', page)

        # Request all of the newest articles matching the search term
        payload = {'sort': 'newest',
                   'end_date': get_end_date(last_date),
                   'api-key': 'YFZKa0q9hHkvaQzlCrZhDyeny6TTLDAj'
                   }

        # Call the API with BaseURL + params and page
        r = call_api(NYT_URL, payload, page)

        # Increment the page before we encounter any potential errors
        page += 1

        # Check to see if the metadata didn't come back. USUALLY happens if
        # page > 100. When it does, reset the whole thing, roll the date back
        # one day, sleep for a couple seconds, then keep going.
        if r.status_code != 200:
            page = 0
            last_date += relativedelta(days=-1)
            print('End Date:', get_end_date(last_date))
            print(r.status_code)
            time.sleep(2)
            continue

        # Get the meta data & documents from the request
        meta, docs = get_response(r)

        # Check if docs are already in the database
        new_docs = remove_previously_scraped(coll, docs)
        if not new_docs: continue

        # Grab only the docs that have these tags
        docs_with_body = get_body_text(new_docs)

        for doc in docs_with_body:
            try:
                # Insert each doc into Mongo
                coll.insert_one(doc)
            except:
                # If there's any error writing it in the db, just move along.
                continue


In [ ]:
if __name__ == "__main__":
    # Initiate Mongo client
    client = pymongo.MongoClient()

    # Access database created for these articles
    db = client.fake_news

    articles = db.nyt_articles

    # Set the initial end date (scraper starts at this date and moves back in
    # time sequentially)
    last_date = datetime.now() + relativedelta(days=-1)
    print(last_date)

    # Pass the database collection and initial end date into main function
    scrape_articles(articles, last_date)

2021-04-16 23:08:00.697381
Page: 0
https://www.nytimes.com/2021/04/16/us/politics/biden-5g-japan.html
https://www.nytimes.com/2021/04/16/us/roger-stone-justice-department-lawsuit.html
https://www.nytimes.com/2021/04/16/well/move/starting-running-jogging.html
https://www.nytimes.com/2021/04/16/world/covid-vaccine-britain-pregnant-women.html
https://www.nytimes.com/2021/04/16/us/politics/justice-department-consent-decrees.html
https://www.nytimes.com/2021/04/16/us/politics/new-york-mayor-race-super-pacs.html
https://www.nytimes.com/2021/04/16/arts/television/helen-mccrory-dead.html
https://www.nytimes.com/2021/04/16/us/patricia-lio-milton-police-assault.html
https://www.nytimes.com/2021/04/16/us/mike-pompeo-state-department-report.html
Page: 1
https://www.nytimes.com/2021/04/16/health/johnson-vaccine-blood-clot-case.html
https://www.nytimes.com/2021/04/16/podcasts/the-daily-newsletter-supreme-court-religion.html
https://www.nytimes.com/2021/04/16/world/canada/coronavirus-cases-vaccines.h

https://www.nytimes.com/2021/04/16/your-money/cars-sale-price-trade-in.html
https://www.nytimes.com/2021/04/16/realestate/americans-have-discovered-the-garden-and-celebrities-want-in.html
https://www.nytimes.com/2021/04/16/your-money/family-foundation-investments.html
https://www.nytimes.com/2021/04/16/business/roaring-twenties-stocks.html
https://www.nytimes.com/2021/04/16/us/bidens-supreme-court-commission-may-weigh-a-range-of-potential-changes-beyond-expanding-seats.html
https://www.nytimes.com/2021/04/16/us/migrant-children-san-diego.html
Page: 13
https://www.nytimes.com/2021/04/16/world/canada/khaleel-seivwright-toronto-homeless.html
https://www.nytimes.com/2021/04/16/us/biden-japan-suga.html
https://www.nytimes.com/2021/04/16/world/asia/afghanistan-forever-war.html
https://www.nytimes.com/2021/04/16/podcasts/ufo-sightings-space-x-sackler-narrated-articles.html
https://www.nytimes.com/2021/04/16/style/gucci-balenciaga-celine-fall-2021.html
https://www.nytimes.com/2021/04/16/learni

https://www.nytimes.com/2021/04/15/world/europe/prince-philip-funeral.html
https://www.nytimes.com/2021/04/15/world/europe/france-security-bill-passes.html
https://www.nytimes.com/2021/04/15/podcasts/still-processing-lil-nas-x-justin-timberlake-apologies.html
https://www.nytimes.com/2021/04/15/world/asia/pakistan-afghanistan-withdrawal.html
Page: 5
https://www.nytimes.com/2021/04/15/us/politics/mike-pence-pacemaker-surgery.html
https://www.nytimes.com/2021/04/15/arts/music/fyre-festival-settlement.html
https://www.nytimes.com/2021/04/15/learning/what-students-are-saying-about-companies-taking-political-stands-podcasting-and-their-life-philosophies.html
https://www.nytimes.com/2021/04/15/briefing/russia-sanctions-tokyo-olympics.html
https://www.nytimes.com/2021/04/15/arts/design/dia-chelsea-reopens-review.html
https://www.nytimes.com/2021/04/15/us/politics/biden-russian-bounties.html
Page: 6
https://www.nytimes.com/2021/04/15/us/placerville-logo-hangtown.html
https://www.nytimes.com/202

https://www.nytimes.com/2021/04/13/health/covid-abortion-pills-mailed.html
https://www.nytimes.com/2021/04/13/sports/baseball/yu-chang-mets-yankees.html
https://www.nytimes.com/2021/04/13/us/politics/afghanistan-troops-withdrawal.html
https://www.nytimes.com/2021/04/13/arts/lincoln-center-plaza-green.html
https://www.nytimes.com/2021/04/13/world/europe/covid-vaccines-astrazeneca-johnson-johnson.html
https://www.nytimes.com/2021/04/13/technology/advertising-children-privacy.html
Page: 8
https://www.nytimes.com/2021/04/13/health/blood-clots-johnson-vaccine.html
https://www.nytimes.com/2021/04/13/world/johnson-covid-vaccine-europe.html
https://www.nytimes.com/2021/04/13/arts/music/eddy-de-pretto-a-tous-les-batards.html
https://www.nytimes.com/2021/04/13/books/review/the-third-pole-mark-synnott.html
https://www.nytimes.com/2021/04/13/world/asia/japan-fukushima-nuclear-wastewater.html
https://www.nytimes.com/2021/04/13/books/review/love-in-color-bolu-babalola.html
https://www.nytimes.com/20

https://www.nytimes.com/2021/04/12/us/kim-potter.html
https://www.nytimes.com/2021/04/12/sports/baseball/yankees-mets.html
https://www.nytimes.com/2021/04/12/business/cinerama-dome-closing.html
https://www.nytimes.com/2021/04/12/us/virginia-officer-army-caron-nazario.html
https://www.nytimes.com/2021/04/12/crosswords/daily-puzzle-2021-04-13.html
https://www.nytimes.com/2021/04/12/business/media/smartmatic-fox-news-lawsuit.html
https://www.nytimes.com/2021/04/12/us/politics/kenya-attack-pentagon.html
https://www.nytimes.com/2021/04/12/us/politics/anne-milgram-dea.html
Page: 19
https://www.nytimes.com/2021/04/12/us/tasers-guns-daunte-wright.html
https://www.nytimes.com/2021/04/12/us/politics/chris-magnus.html
https://www.nytimes.com/2021/04/12/pageoneplus/corrections-april-13-2021.html
https://www.nytimes.com/2021/04/12/business/media/reuters-editor-Alessandra-Galloni.html
https://www.nytimes.com/2021/04/12/todayspaper/quotation-of-the-day-japans-new-hero-whether-he-likes-it-or-not.html


...

Page: 0
End Date: 20040307
429
Page: 0
End Date: 20040306
429
Page: 0
End Date: 20040305
429
Page: 0
End Date: 20040304
429
Page: 0
End Date: 20040303
429
Page: 0
End Date: 20040302
429
Page: 0
End Date: 20040301
429
Page: 0
End Date: 20040229
429
Page: 0
End Date: 20040228
429
Page: 0
End Date: 20040227
429
Page: 0
End Date: 20040226
429
Page: 0
End Date: 20040225
429
Page: 0
End Date: 20040224
429
Page: 0
End Date: 20040223
429
Page: 0
End Date: 20040222
429
Page: 0
End Date: 20040221
429
Page: 0
End Date: 20040220
429
Page: 0
End Date: 20040219
429
Page: 0
End Date: 20040218
429
Page: 0
End Date: 20040217
429
Page: 0
End Date: 20040216
429
Page: 0
End Date: 20040215
429
Page: 0
End Date: 20040214
429
Page: 0
End Date: 20040213
429
Page: 0
End Date: 20040212
429
Page: 0
End Date: 20040211
429
Page: 0
End Date: 20040210
429
Page: 0
End Date: 20040209
429
Page: 0
End Date: 20040208
429
Page: 0
End Date: 20040207
429
Page: 0
End Date: 20040206
429
Page: 0
End Date: 20040205
429
Page: 0


Page: 0
End Date: 20030616
429
Page: 0
End Date: 20030615
429
Page: 0
End Date: 20030614
429
Page: 0
End Date: 20030613
429
Page: 0
End Date: 20030612
429
Page: 0
End Date: 20030611
429
Page: 0
End Date: 20030610
429
Page: 0
End Date: 20030609
429
Page: 0
End Date: 20030608
429
Page: 0
End Date: 20030607
429
Page: 0
End Date: 20030606
429
Page: 0
End Date: 20030605
429
Page: 0
End Date: 20030604
429
Page: 0
End Date: 20030603
429
Page: 0
End Date: 20030602
429
Page: 0
End Date: 20030601
429
Page: 0
End Date: 20030531
429
Page: 0
End Date: 20030530
429
Page: 0
End Date: 20030529
429
Page: 0
End Date: 20030528
429
Page: 0
End Date: 20030527
429
Page: 0
End Date: 20030526
429
Page: 0
End Date: 20030525
429
Page: 0
End Date: 20030524
429
Page: 0
End Date: 20030523
429
Page: 0
End Date: 20030522
429
Page: 0
End Date: 20030521
429
Page: 0
End Date: 20030520
429
Page: 0
End Date: 20030519
429
Page: 0
End Date: 20030518
429
Page: 0
End Date: 20030517
429
Page: 0
End Date: 20030516
429
Page: 0


Page: 0
End Date: 20020924
429
Page: 0
End Date: 20020923
429
Page: 0
End Date: 20020922
429
Page: 0
End Date: 20020921
429
Page: 0
End Date: 20020920
429
Page: 0
End Date: 20020919
429
Page: 0
End Date: 20020918
429
Page: 0
End Date: 20020917
429
Page: 0
End Date: 20020916
429
Page: 0
End Date: 20020915
429
Page: 0
End Date: 20020914
429
Page: 0
End Date: 20020913
429
Page: 0
End Date: 20020912
429
Page: 0
End Date: 20020911
429
Page: 0
End Date: 20020910
429
Page: 0
End Date: 20020909
429
Page: 0
End Date: 20020908
429
Page: 0
End Date: 20020907
429
Page: 0
End Date: 20020906
429
Page: 0
End Date: 20020905
429
Page: 0
End Date: 20020904
429
Page: 0
End Date: 20020903
429
Page: 0
End Date: 20020902
429
Page: 0
End Date: 20020901
429
Page: 0
End Date: 20020831
429
Page: 0
End Date: 20020830
429
Page: 0
End Date: 20020829
429
Page: 0
End Date: 20020828
429
Page: 0
End Date: 20020827
429
Page: 0
End Date: 20020826
429
Page: 0
End Date: 20020825
429
Page: 0
End Date: 20020824
429
Page: 0


Page: 0
End Date: 20020102
429
Page: 0
End Date: 20020101
429
Page: 0
End Date: 20011231
429
Page: 0
End Date: 20011230
429
Page: 0
End Date: 20011229
429
Page: 0
End Date: 20011228
429
Page: 0
End Date: 20011227
429
Page: 0
End Date: 20011226
429
Page: 0
End Date: 20011225
429
Page: 0
End Date: 20011224
429
Page: 0
End Date: 20011223
429
Page: 0
End Date: 20011222
429
Page: 0
End Date: 20011221
429
Page: 0
End Date: 20011220
429
Page: 0
End Date: 20011219
429
Page: 0
End Date: 20011218
429
Page: 0
End Date: 20011217
429
Page: 0
End Date: 20011216
429
Page: 0
End Date: 20011215
429
Page: 0
End Date: 20011214
429
Page: 0
End Date: 20011213
429
Page: 0
End Date: 20011212
429
Page: 0
End Date: 20011211
429
Page: 0
End Date: 20011210
429
Page: 0
End Date: 20011209
429
Page: 0
End Date: 20011208
429
Page: 0
End Date: 20011207
429
Page: 0
End Date: 20011206
429
Page: 0
End Date: 20011205
429
Page: 0
End Date: 20011204
429
Page: 0
End Date: 20011203
429
Page: 0
End Date: 20011202
429
Page: 0


ConnectionError: HTTPConnectionPool(host='api.nytimes.com', port=80): Max retries exceeded with url: /svc/search/v2/articlesearch.json?sort=newest&end_date=20010614&api-key=YFZKa0q9hHkvaQzlCrZhDyeny6TTLDAj&page=0 (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000181CA7049D0>: Failed to establish a new connection: [WinError 10060] A connection attempt failed because the connected party did not properly respond after a period of time, or established connection failed because connected host has failed to respond'))